In [1]:
import folium
import branca

# Visualisation of Vinex neighbourhoods and categories and 

This short document presents an overview of the geographical categories that will use in the study on the effect of the Vinex. Vinex locations are the 'uitleg-locaties', as defined in the Ruimtelijke Metamorfose van Nederland, and are coupled to the buurt definition from the CBS classification of 2013. In our study we want to look at long-term effects of the designated areas in a counterfactual setup. We discussed the following three options:

1. Treatment: Vinex; control: not-Vinex, paired with Vinex neighbourhood of same/similar density
2. Treatment: Vinex; control: not-Vinex, paired with Vinex neighbourhood in the same stadsgewest
3. Treatment: Vinex; control: Vinex of another type (tbd)


## Data
Sources:

* Vinex categories from the Ruimtelijke Metamorfose
* Buurt en Wijk Kaarten 2013
* Gebiedsindeling 2013 from CBS open data

Massaging and general data wrangling:

* collapse the five categories into three
* merge Vinex typology with buurt en wijk kaarten
* add Stadsgewesten classification to merged data


In [2]:
%run -i vinex_read_data.py

## Maps

Description here...

In [3]:
## definition and function for creating map

## mid point of Netherlands
yx_point = [bw_shp['geometry'].centroid.y.mean(),
            bw_shp['geometry'].centroid.x.mean()] 

## from https://geospatialawarenesshub.com/blog/make-interactive-choropleth-maps/
def create_folium_map(gdf, n_cats, target_var, display_vars):
    # make sure the index is correct
    gdf['idx'] = np.arange(0,len(gdf))
    gdf = gdf.set_index('idx') 
    # base map
    m = folium.Map(location=yx_point, zoom_start=11, tiles='cartodbpositron')
    # create color palette
    colormap = branca.colormap.linear.YlGnBu_09.to_step(n_cats).scale(0, n_cats-1)
    # create dictionary
    #vinex_dict = vinex_merged.set_index('BU_CODE')['Vinex_cat']
    v_dict = gdf.set_index('BU_CODE')[target_var]
    # style function for geojson
    def style_function(feature):
        v_d = v_dict.get(int(feature['id']), None)
        return {
            'fillColor': '#black' if v_d is None else colormap(v_d),
            'color': 'black',
            'weight': 0.2,
            'dashArray': '5, 5',
            'fillOpacity': 0.6,
        }
    x=folium.GeoJson(
        gdf,
        name= target_var,
        style_function=style_function,
        highlight_function= None,
        tooltip=(gdf[i] for i in gdf[display_vars])
    ).add_to(m)
    x.add_child(folium.features.GeoJsonTooltip(display_vars))
    folium.LayerControl().add_to(m)

    return m



In [4]:
## Map of Vinex typology
m1 = create_folium_map(vinex_merged, 3, 'Vinex_cat', ['Vinex_naam', 'BU_NAAM', 'Vinex_type_upd'])
#m1.save('/home/trond/Documents/wonen_werken/output/vinex_typology.html')
m1

In [2]:
## Map of Stadsgewesten
#bw_shp[bw_shp['Stadsgewest_naam'] != 'Niet van toepassing'].head()
## 
# conds = (bw_shp['Stadsgewest_naam'] != 'Niet van toepassing') & (bw_shp['WATER'] == 'NEE')
# m2 = create_folium_map(
#     bw_shp[conds],
#     2,
#     'Vinex',
#     ['BU_NAAM', 'Vinex_naam']
# )
#bw_shp[bw_shp['Vinex_type'].notna()]
#m2

In [3]:
# conds = (bw_shp['STED'] == 3) & (bw_shp['WATER'] == 'NEE')
# m3 = create_folium_map(
#     bw_shp[conds],
#     2,
#     'Vinex',
#     ['BU_NAAM', 'Vinex_naam']
# )
#bw_shp[bw_shp['Vinex_type'].notna()]
#m3